In [1]:
import sympy

We attempt to model motion as a series of piecewise-constant jerk segments (where jerk is $d^4p \over dp^4$)

For an individual segment, we have:

In [66]:
sympy.var("p,v,a,j,t,v0,a0, a_max, v_max, j_max", real=True)
g_a0 = a0
g_v0 = v0
g_t = t

In [67]:
def seg_d(j=j, a0=a0, v0=v0, t=t, p0=0):
    res = dict(
        dt = t,
        da = t * j,
        dv = j * t**2 / 2 + a0*t,
        dp = j*t**3/6 + a0 * t**2 / 2 + v0 * t
    )
    res["ae"] = res["da"] + a0
    res["ve"] = res["dv"] + v0
    res["pe"] = p0 + res["dp"]
    return dict((k, v.simplify()) for k,v in res.items())
seg_p = seg_d()["dp"]

In [68]:
sympy.Eq(p, seg_p)

Eq(p, t*(3*a0*t + j*t**2 + 6*v0)/6)

We have three machine limits to consider at this point: we have a maximum jerk (derived from the shock limits of the system), maximum acceleration (derived from the torque limits of the servos), and maximum velocity (from the frequency at which we update the steppers). We can ignore the position bounds at this point; the commands to this stage of the motion planner are simply "move by ΔX,ΔY", and so we can assume that the source of those commands will never ask us to move outside the range of motion.

This leaves us with the following general motion profile for a single linear move:
1. $j>0$; Increase acceleration to $a_{max}$
2. $j=0$; continue accelerating at $a_{max}$ to somewhat before $v_{max}$
3. $j<0$; reduce acceleration to 0 to reach constant velocity $v_{max}$
4. $j=0$; proceed at constant velocity to decelleration point
5. $j<0$; begin decelleration to $-a_{max}$
6. $j=0$; decelerate at max rate to just before 0 velocity
7. $j>0$; decrease decelleration until $v=0$

Let's call the time taken for segment $n$ "$t_n$". Note that, through a simple coordinate transform, $t_1=t_3=t_5=t_7$. Further, $t_2=t_6$. We'll rename these to $t_j$ and $t_a$ (for constant jerk and constant accelleration), respectively, and introduce $t_v = t_4$ for consistency.


There are several possible degenerate cases:

* The move is too short to reach $v_{max}$. In this case, we lower $v_max$ accordingly and set $t_v=0$.
* $a_{max}$ is unreachable given the maximum velocity. This results in $t_a$ both being 0 for all moves and the calculation proceeding with lowered $a_{max}$

Note that the first situation can give rise to the second.

We can handle these degenerate situations using the following algorithm:

1. Assume the most general form of the profile. In this case, all but stage 4 is constant-time, so solve for $t_v$
2. If the calculated $t_v < 0$, calculate the actual $v_{max}$ and recalculate $t_a$ holding $t_j$ constant and $t_v=0$.
3. If $t_a<0$, recalculate $t_j$ holding $t_v=t_a=0$

This means that to solve the motion equations, we need a couple of closed-form solutions:

In [96]:
# Time and position calculations for general form
t_a = a_max / j_max
p1s1 = seg_d(j=j_max, a0=0, v0=0, t=t_a)
p1s1

{'dt': a_max/j_max,
 'da': a_max,
 'dv': a_max**2/(2*j_max),
 'dp': a_max**3/(6*j_max**2),
 'ae': a_max,
 've': a_max**2/(2*j_max),
 'pe': a_max**3/(6*j_max**2)}

In [97]:
p1s3 = seg_d(j=-j_max, a0=p1s1["ae"], t=t_a)
p1s3_v0 = sympy.solve(p1s3["ve"] - v_max, v0)[0]
p1s3 = seg_d(j=-j_max, a0=p1s1["ae"], t=t_a, v0 = p1s3_v0)
p1s3

{'dt': a_max/j_max,
 'da': -a_max,
 'dv': a_max**2/(2*j_max),
 'dp': -a_max**3/(6*j_max**2) + a_max*v_max/j_max,
 'ae': 0,
 've': v_max,
 'pe': -a_max**3/(6*j_max**2) + a_max*v_max/j_max}

In [98]:
t_v = (p1s3_v0 - p1s1["ve"]) / p1s1["ae"]
p1s2 = seg_d(j = 0, a0=p1s1["ae"], v0 = p1s1["ve"], t = t_v, p0=p1s1["pe"])
p1s3["pe"] = (p1s3["dp"] + p1s2["pe"]).simplify()
p1s2

{'dt': -a_max/j_max + v_max/a_max,
 'da': 0,
 'dv': -a_max**2/j_max + v_max,
 'dp': v_max*(-a_max**2 + j_max*v_max)/(2*a_max*j_max),
 'ae': a_max,
 've': -a_max**2/(2*j_max) + v_max,
 'pe': a_max**3/(6*j_max**2) - a_max*v_max/(2*j_max) + v_max**2/(2*a_max)}

In [99]:
p1s1_dp.subs(a_max, None)

a_max**3/(6*j_max**2)

In [100]:
p1s3["pe"]

v_max*(a_max**2 + j_max*v_max)/(2*a_max*j_max)

In [108]:
(p1s3["pe"] - sum(x["dp"] for x in [p1s5, p1s6, p1s7])).simplify()

0

In [106]:
p1s5 = seg_d(j=-j_max, a0=0, v0=v_max, t=t_a, p0=p1s3["pe"])
p1s6 = seg_d(j=0, a0=p1s5["ae"], v0=p1s5["ve"], t=t_v, p0=p1s5["pe"])
p1s7 = seg_d(j=j_max, a0=p1s6["ae"], v0=p1s6["ve"], t=t_a, p0=p1s6["pe"])

In [107]:
p1s7

{'dt': a_max/j_max,
 'da': a_max,
 'dv': -a_max**2/(2*j_max),
 'dp': a_max**3/(6*j_max**2),
 'ae': 0,
 've': 0,
 'pe': a_max*v_max/j_max + v_max**2/a_max}

In [109]:
p1s3

{'dt': a_max/j_max,
 'da': -a_max,
 'dv': a_max**2/(2*j_max),
 'dp': -a_max**3/(6*j_max**2) + a_max*v_max/j_max,
 'ae': 0,
 've': v_max,
 'pe': v_max*(a_max**2 + j_max*v_max)/(2*a_max*j_max)}